# Pratical session 1 of Quantum Information and Dynamics

## General comments

The practical session uses this notebook. It should be returned by Friday December 22 at the address 
[Brigitte.Bidegaray@univ-grenoble-alpes.fr](mailto:Brigitte.Bidegaray@univ-grenoble-alpes.fr).
The name of the file should at least contain your familly name. 
If your file is more that one 1Mo, please consider deleting the execution results (we will in any case rerun the notebook).

The general framework (physical constants, input wave...) are given and then you should complete the cells with code to answer the questions <b>and</b> add Markdown cells to comment the numerical results.  

# Numerical resolution of the von Neumann equation

This practical concerns the numerical resolution of the equation
\begin{align*}
i \hbar \frac{\mathrm{d}}{\mathrm{d} t} \rho(t) &= [H_0 + pE(t), \rho(t)] + i \hbar Q(\rho(t)),\\
 \rho(0)&=\rho_0,
\end{align*}
where we consider
- a free Hamiltonian: $H_0$ is a diagonal matrix made of the energy levels $\{\varepsilon_j\}$ of the system,
-  an electric interaction part: $p$ is a polarizability matrix and $E$ a given electric field,
- population relaxations: $Q(\rho)_{jj} 
= \sum_{\ell\neq j} W_{\ell j} \rho_{\ell\ell} - \sum_{\ell\neq j} W_{j \ell} \rho_{jj}$ with $W_{j \ell} = W_{\ell j} e^{\beta(\varepsilon_j - \varepsilon_\ell)}$,
- coherence relaxations: $Q(\rho)_{jk}=-\gamma_{jk} \rho_{jk}$ for $j\neq k$ with $\gamma_{jk}=\gamma_{kj}\in\mathbb{R}$.

Notice that, compared to the course, we do not consider here a dimensionless equation but we take into account all physical constants.  

In [ ]:
import numpy as np
from scipy.linalg import expm
import matplotlib.pyplot as plt

In [ ]:
# Physical constants
hbar        = 1.05457*1e-34  # [J s]  reduced Planck's constant
charge_elem = 1.60218*1e-19  # [C]    Electron's charge
kb          = 1.38066*1e-23  # [J/K]  Boltzmann's constant

In [ ]:
# Dimension of the matrix density
N_band = 3

# H_0 parameters (Eg is the gap energy)
Eg = 0.02 * charge_elem              
energies = np.array([0, 3, 4]) * Eg
H0 = np.diag(energies)

# Polarizability matrix
pmax = 1e-29
p_mat = (np.ones((N_band, N_band)) - np.eye(N_band)) * pmax

# Population relaxations
temperature = 300
W = 2e12

W_mat = np.zeros((N_band, N_band))
for j in range(N_band):
    for k in range(j):
        W_mat[j, k] = W_mat[k, j] * np.exp(-(energies[j] - energies[k]) / (kb*temperature))
    for k in range(j+1, N_band):
        W_mat[j, k] = W

# I. Self-induced transparency test case

For the moment we do not consider relaxation terms and we concentrate on the commutator part.

\begin{align*}
i \hbar \frac{\mathrm{d}}{\mathrm{d} t} \rho(t) &= [H_0, \rho(t)] +E(t)[p, \rho(t)],\quad t\in]0,T_{max}],\\
 \rho(0)&=\rho_0. 
\end{align*}

We introduce a uniform time discretization using $N_t$ points: $t_p = p\delta t$, for $p = 0, \dots, N_t-1$ where $\delta t = \frac{T_{max}}{N_t-1}$. 

We are looking for $\rho^p$ an approximation of $\rho(t^p)$. 

We consider a initial density matrix $\rho_0$ without coherences ($(\rho_0)_{jk}=0$ for $j \neq k$).


In [ ]:
# Time discretization
Nt = 5001
Tmax = 4e-12
deltat = Tmax / (Nt-1)
t = np.linspace(0, Tmax, Nt)

# Initialisation
rho_init = np.zeros(N_band)
rho_init[-1] = 1

# rho variable
rho = np.zeros((N_band, N_band, Nt), dtype=complex)
rho[:,:,0] = np.diag(rho_init)

## Self-induced transparency

Self-induced transparency is a phenomenon where a wave, in interaction with the media, propagates unchanged. 
It is designed for the bi-directional coupling of Maxwell equations and Bloch equation. Here we will use a wave that can propagate in this way. Its energy is designed such that the matter experiences a integer number of inversions, where an inversion is a transition between a state where only one level is populated, to another state where only another level is populated.

## Incident field

To this aim we use the following field:
\begin{equation}
E(t) = \frac{k\hbar}{p_{\rm max}\tau_p} \frac{\sin\left(\frac{E_{\rm gap} (t-t_0)}{\hbar}\right)}{\cosh\left(\frac{t-t_0}{\tau_p}\right)}.
\end{equation}
This type of field is called a wave paquet. The integer $k$ is the number of total inversions.

In [ ]:
# Incident field
def incident_field(t):
    omega = Eg / hbar
    tau_p = 15e-14
    t0 = 15 * tau_p
    k = 1
    E0 = k * hbar / (pmax * tau_p)
    return E0 * np.sin(omega * (t-t0)) / np.cosh((t-t0) / tau_p)

plt.plot(t, incident_field(t))
plt.xlabel('t')
plt.ylabel('E(t)');

### Question I.1.

Define four functions:
* `difference_energies` computes the matrix $A$ such that $([H_0,\rho])_{jk}=A_{jk}\rho_{jk}$,
* `S_R` is the propagator over one time step associated to the relaxation--nutation (for the moment, only nutation) operator,
* `S_E` is the propagator over one time step associated to the interaction with the wave,
* `bloch_splitting` is one step of Lie or Strang splitting (separating $H_0$ and $pE(t)$) between time $t_n$ and time $t_n + \delta t$. 

In [ ]:
#def difference_energies(energies):
#    # T0 DO
    
#def S_R(rho, eps_mat, dt):    
#    # T0 DO

#def S_E(rho, V, dt):
#    # TO DO
    
#def bloch_splitting(rho, tn, eps_mat, dt):
#    # TO DO
    

### Question I.2.

Observe the self-induced transparency phenomenon. Play with the number of total inversions, the initial state and the energy levels (possibly also the number of bands).

In [ ]:
# functions difference_energies and bloch_splitting have to be created
eps_mat = difference_energies(energies)
for p in range(Nt-1):
    rho[:,:,p+1] = bloch_splitting(rho[:,:,p], t[p], eps_mat, deltat)
    
for j in range(N_band):
    plt.plot(t, np.real(rho[j,j,:]), label=r"$\rho$"+f"{j+1}{j+1}")
plt.xlabel('t');
plt.ylabel('populations');
plt.legend();

### Question I.3.

Check numerically the preservation of trace, Hermicity and positiveness of $\rho$.

In [ ]:
### TO DO

# II. Analysis of classical methods

### Question II.1. 

For the previous test case, implement and test some classical methods such that forward Euler, backward Euler, Crank-Nicolson. For schemes with an implicit part, use a fixed point method.

In [ ]:
### TO DO

### Question II.2.

Analyze the quality of the implemented schemes, for instance by studying the time evolution of the Frobenius norm $\|\rho\|_2$.

In [ ]:
### TO DO

# III. Population relaxations

We now consider only the relaxation term on populations

\begin{align*}
i \hbar \frac{\mathrm{d}}{\mathrm{d} t} \rho(t)_{jj} &= i \hbar Q(\rho(t))_{jj},\\
 \rho_{jj}(0)&=(\rho_0)_{jj},
\end{align*}

### Question III.1. 

Compute the Gibbs state of the system

In [ ]:
### TO DO

### Question III.2. 

Build the matrix $\tilde W$ and compute the time evolution of populations. Check that it relaxes to the Gibbs state. Play with different initial states.

In [ ]:
### TO DO

### Question III.3.  

Compute the time evolution of the von Neumann entropy. Comment the results.

In [ ]:
### TO DO

# IV. Full von Neumann equation


We now consider the full equation
\begin{align*}
i \hbar \frac{\mathrm{d}}{\mathrm{d} t} \rho(t) &= [H_0 + pE(t), \rho(t)] + i \hbar Q(\rho(t)),\\
 \rho(0 )&= \rho_0.
\end{align*}


### Question IV.1. 

Implement a splitting method to take into account all the terms. Test it on the induced transparency test case. 

To validate the code, you could compute the solution with the relaxation terms but choose $\gamma_{jk}=0$ and/or $W=0$. 

In [ ]:
### TO DO

### Question IV.2. 

At your convenience, play with the parameters and comment the results (from a physical or a numerical point of view). For instance, you could successively get rid of one term to explain its contribution.

In [ ]:
# TO DO